# 使用 Milvus 和 DeepSeek 构建 RAG

DeepSeek 帮助开发者使用高性能语言模型构建和扩展 AI 应用。它提供高效的推理、灵活的 API 以及先进的专家混合 (MoE) 架构，用于强大的推理和检索任务。

在本教程中，我们将展示如何使用 Milvus 和 DeepSeek 构建一个检索增强生成 (RAG) 管道。

## 准备工作

### 依赖与环境

In [1]:
!pip install "pymilvus[model]==2.5.10" openai==1.82.0 requests==2.32.3 tqdm==4.67.1 torch==2.7.0

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple


---

In [2]:
import os

# 从环境变量获取 DeepSeek API Key
api_key = os.getenv("DEEPSEEK_API_KEY")

### 准备数据

我们使用 Milvus 文档 2.4.x 中的 FAQ 页面作为我们 RAG 中的私有知识库，这是一个简单 RAG 管道的良好数据源。

下载 zip 文件并将文档解压到 `milvus_docs` 文件夹。

**建议在命令行执行下面命令**

In [3]:
#!wget https://github.com/milvus-io/milvus-docs/releases/download/v2.4.6-preview/milvus_docs_2.4.x_en.zip
#!unzip -q milvus_docs_2.4.x_en.zip -d milvus_docs

我们从 `milvus_docs/en/faq` 文件夹加载所有 markdown 文件。对于每个文档，我们简单地使用 "# " 来分割文件中的内容，这样可以大致分离出 markdown 文件中每个主要部分的内容。

In [4]:
from glob import glob

text_lines = []

# for file_path in glob("milvus_docs/en/faq/*.md", recursive=True):
for file_path in glob("mfd.md", recursive=True):
    with open(file_path, "r") as file:
        file_text = file.read()
        
    # text_lines += file_text.split("# ")
    text_lines += file_text.split("**")


In [54]:
len(text_lines)

30

### 准备 LLM 和 Embedding 模型

DeepSeek 支持 OpenAI 风格的 API，您可以使用相同的 API 进行微小调整来调用 LLM。

In [30]:
from openai import OpenAI
import os

api_key = os.getenv("DEEPSEEK_API_KEY")
deepseek_client = OpenAI(
    api_key=api_key,
    base_url="https://api.deepseek.com/v1",  # DeepSeek API 的基地址
)

定义一个 embedding 模型，使用 `milvus_model` 来生成文本嵌入。我们以 `DefaultEmbeddingFunction` 模型为例，这是一个预训练的轻量级嵌入模型。

In [ ]:
# from pymilvus import model as milvus_model

# embedding_model = milvus_model.DefaultEmbeddingFunction()

from pymilvus import model as milvus_model

api_key = ""

# OpenAI国内代理 https://api.apiyi.com/token 
embedding_model = milvus_model.dense.OpenAIEmbeddingFunction(
    model_name='text-embedding-v4', # Specify the model name
    api_key=api_key, # Provide your OpenAI API key
    base_url="https://dashscope.aliyuncs.com/compatible-mode/v1",
    dimensions=512
)




/home/zq/projects/DEEPSEEK-QuickStart/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


生成一个测试嵌入并打印其维度和前几个元素。

In [10]:
test_embedding = embedding_model.encode_queries(["This is a test"])[0]
embedding_dim = len(test_embedding)
print(embedding_dim)
# embedding之后的长度是512位，我们把前10位给取出来
print(test_embedding[:10])

512
[-0.02423961  0.03560013  0.03585002 -0.03654203 -0.01879002 -0.00445242
 -0.00890003  0.0340431  -0.08219554  0.18115313]


In [89]:
test_embedding_0 = embedding_model.encode_queries(["That is a test"])[0]
print(test_embedding_0[:10])

[-0.02432832 -0.00198     0.04136878 -0.0215874  -0.01044843 -0.04005143
  0.01617993  0.08154769 -0.04381223  0.17329416]


## 将数据加载到 Milvus

### 创建 Collection

In [11]:
from pymilvus import MilvusClient

milvus_client = MilvusClient(uri="./milvus_demo.db")

collection_name = "my_rag_collection"

关于 `MilvusClient` 的参数：

*   将 `uri` 设置为本地文件，例如 `./milvus.db`，是最方便的方法，因为它会自动利用 Milvus Lite 将所有数据存储在此文件中。
*   如果您有大规模数据，可以在 Docker 或 Kubernetes 上设置性能更高的 Milvus 服务器。在此设置中，请使用服务器 URI，例如 `http://localhost:19530`，作为您的 `uri`。
*   如果您想使用 Zilliz Cloud（Milvus 的完全托管云服务），请调整 `uri` 和 `token`，它们对应 Zilliz Cloud 中的 Public Endpoint 和 Api key。

检查 collection 是否已存在，如果存在则删除它。

In [12]:
if milvus_client.has_collection(collection_name):
    milvus_client.drop_collection(collection_name)

创建一个具有指定参数的新 collection。

如果我们不指定任何字段信息，Milvus 将自动创建一个默认的 `id` 字段作为主键，以及一个 `vector` 字段来存储向量数据。一个保留的 JSON 字段用于存储非 schema 定义的字段及其值。

`metric_type` (距离度量类型):
     作用：定义如何计算向量之间的相似程度。
     例如：`IP` (内积) - 值越大通常越相似；`L2` (欧氏距离) - 值越小越相似；`COSINE` (余弦相似度) - 通常转换为距离，值越小越相似。
     选择依据：根据你的嵌入模型的特性和期望的相似性定义来选择。

 `consistency_level` (一致性级别):
     作用：定义数据写入后，读取操作能多快看到这些新数据。
     例如：
         `Strong` (强一致性): 总是读到最新数据，可能稍慢。
         `Bounded` (有界过期): 可能读到几秒内旧数据，性能较好 (默认)。
         `Session` (会话一致性): 自己写入的自己能立刻读到。
         `Eventually` (最终一致性): 最终会读到新数据，但没时间保证，性能最好。
     选择依据：在数据实时性要求和系统性能之间做权衡。

简单来说：
 `metric_type`：怎么算相似。
 `consistency_level`：新数据多久能被读到。

In [13]:
milvus_client.create_collection(
    collection_name=collection_name,
    dimension=embedding_dim,
    metric_type="IP",  # 内积距离
    consistency_level="Strong",  # 支持的值为 (`"Strong"`, `"Session"`, `"Bounded"`, `"Eventually"`)。更多详情请参见 https://milvus.io/docs/consistency.md#Consistency-Level。
)

### 插入数据

遍历文本行，创建嵌入，然后将数据插入 Milvus。

这里有一个新字段 `text`，它是在 collection schema 中未定义的字段。它将自动添加到保留的 JSON 动态字段中，该字段在高级别上可以被视为普通字段。

In [14]:
from tqdm import tqdm

data = []
print(text_lines.__len__())
# 将Faq插入到向量数据库当中
# doc_embeddings = embedding_model.encode_documents(text_lines)
batch_size = 10
doc_embeddings = []
for i in range(0, len(text_lines), batch_size):
    doc_embeddings.extend(embedding_model.encode_documents(text_lines[i:i+batch_size]))

# 原始文本，通过tqdm创建了 embeddings 进度条
for i, line in enumerate(tqdm(text_lines, desc="Creating embeddings")):
    print(doc_embeddings[i], line)
    data.append({"id": i, "vector": doc_embeddings[i], "text": line})

milvus_client.insert(collection_name=collection_name, data=data)

775


Creating embeddings:  21%|██        | 161/775 [00:00<00:00, 804.48it/s]

[ 1.37034012e-02  1.12059209e-02  7.58410767e-02 -1.55554647e-02
 -3.90617102e-02  2.35343054e-02  2.22060569e-02  8.75521079e-02
 -1.19504884e-01 -1.96805168e-02 -7.25110993e-02 -6.37558922e-02
 -9.01711881e-02 -6.64498061e-02  4.15311269e-02 -1.01769969e-01
 -4.92012911e-02 -1.29307732e-01  4.64699641e-02 -2.27485821e-02
 -2.32794136e-03  2.91466191e-02  3.92113701e-02  1.39278937e-02
 -1.35514012e-03 -4.20689723e-03  1.46967813e-01 -7.26981834e-02
  3.82759832e-02  5.91163784e-02 -6.52431557e-03 -1.07382284e-02
 -4.80039977e-02 -3.52079198e-02  1.63224805e-02  4.74006729e-03
  1.20723220e-04  6.22966923e-02 -6.76283892e-03 -5.23523719e-04
  5.03611676e-02 -4.87523042e-02  3.21959779e-02 -4.24290970e-02
 -4.77795042e-02  3.44783179e-02  3.85378934e-02  3.75463851e-02
 -4.64699641e-02  4.08950634e-02  2.53676623e-02  5.38782170e-03
 -4.69937809e-02  6.64498061e-02  2.86415108e-02 -8.17153007e-02
  1.53870955e-02 -4.01841700e-02 -2.34220587e-02  2.06907336e-02
  1.69491898e-02  5.76571

Creating embeddings:  42%|████▏     | 323/775 [00:00<00:00, 794.78it/s]

[-5.41865341e-02 -4.38030250e-02  1.09911367e-01  3.93804200e-02
 -4.73795682e-02  8.52313079e-03  1.08526900e-01  6.53391927e-02
 -4.92255241e-02  2.93814857e-02 -9.33193893e-04 -4.87928791e-03
  8.53755232e-03 -1.94690805e-02  1.63059551e-02 -1.02142967e-01
 -2.13438794e-02 -1.39062107e-01  5.60036488e-03 -2.65115988e-03
 -5.69170155e-02 -1.37773789e-02  3.44963260e-02  1.92191061e-02
  3.89958471e-02  1.96709819e-02  8.95289257e-02 -4.61008586e-03
 -2.22860873e-02  5.94167458e-03 -8.05298835e-02 -4.49182913e-02
 -4.36491966e-02 -1.65246823e-03 -2.81316191e-02  4.52259518e-02
 -9.14517939e-02  4.18032408e-02  2.16899980e-02 -6.83004186e-02
 -7.36459997e-03 -1.48830302e-02  3.20350491e-02 -3.91881317e-02
 -5.92629164e-02  1.15141578e-01  5.91475442e-02  5.69554716e-02
  2.73816995e-02 -6.62621707e-02 -9.30670090e-03 -5.69939278e-02
  1.42869400e-02  2.50934809e-02  1.31428307e-02 -3.19389068e-02
  3.02852355e-02  3.08140251e-03  2.68625226e-02  1.22871529e-02
 -1.02104507e-02  3.86112

...

Creating embeddings:  83%|████████▎ | 647/775 [00:00<00:00, 800.17it/s]

[-1.93552040e-02 -9.20660049e-02  7.75680020e-02  5.41283339e-02
 -6.84791505e-02  1.19130174e-02  9.16244462e-02  1.19222164e-01
 -6.33275732e-02 -1.48015795e-02 -2.29061116e-03 -5.83967827e-02
  2.59188632e-03 -5.57841994e-02 -1.11310817e-02 -6.87735304e-02
  5.03014512e-02 -1.31512359e-01 -2.87200306e-02  3.97039242e-02
 -5.14697563e-03  4.76888679e-02  3.23997289e-02  1.31181180e-02
 -4.62537855e-02  3.34300436e-02  8.29403624e-02 -1.85364708e-02
 -1.91712193e-02 -2.73907417e-03 -3.74777094e-02 -1.12451524e-01
 -8.24987963e-02 -4.66953479e-02 -1.23729799e-02  4.58858162e-02
 -6.76696151e-02  4.71369140e-02  1.71289872e-02 -5.78080304e-02
 -2.79840920e-02 -5.48642762e-02 -5.62625602e-02 -1.77269373e-02
 -2.98791360e-02 -4.75784764e-02  1.05165727e-01  3.96303311e-02
 -1.10758869e-02 -6.32539839e-02 -2.17838027e-02 -3.87840010e-02
 -1.72577761e-02  6.50938302e-02  1.01743611e-02 -4.69897240e-02
  3.34484428e-02 -2.06798948e-02  5.28496411e-03  3.26021127e-02
 -2.36236509e-02  1.75429

Creating embeddings: 100%|██████████| 775/775 [00:00<00:00, 785.12it/s]


[ 1.47785563e-02 -6.78649321e-02  6.67757913e-02  1.89567376e-02
 -7.88690448e-02  2.24964563e-02  8.33758488e-02  1.30321711e-01
 -5.31051569e-02  3.12847197e-02 -3.40263583e-02 -2.90688761e-02
  9.99946799e-03 -5.98653592e-02 -1.73112855e-03 -7.78925717e-02
  2.51629818e-02 -1.32124424e-01  1.86656732e-02 -3.21673043e-02
 -5.92268966e-02  4.19508219e-02  2.60080062e-02  1.96609255e-02
 -4.60444987e-02  6.73015863e-02  5.82504235e-02 -2.37733833e-02
 -2.45808531e-02  3.07964850e-02 -5.29924855e-02 -5.29173724e-02
 -8.95351470e-02 -4.83354591e-02 -7.31604248e-02  4.44295630e-02
 -1.77830923e-02  9.37414914e-02 -1.02717541e-02 -5.93771227e-02
 -5.96681889e-03 -3.63548733e-02 -3.49089429e-02 -6.50857389e-02
 -4.99879532e-02 -2.14824248e-02  7.34608844e-02  3.58103029e-02
  1.08632725e-02 -4.47300151e-02  3.28057669e-02 -2.80736238e-02
 -9.72718187e-03  7.85685927e-02  1.11261685e-03  1.45156598e-02
  7.63903037e-02 -3.91716249e-02  1.64873861e-02  4.15376984e-02
 -1.16425734e-02 -4.57252

{'insert_count': 775, 'ids': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 

## 构建 RAG

### 检索查询数据

我们指定一个关于 Milvus 的常见问题。

In [20]:
# question = "How is data stored in milvus?"
# question = "How is data stored in milvus?"
question = "担保物权消灭的"

在 collection 中搜索该问题，并检索语义上最匹配的前3个结果。

In [21]:
search_res = milvus_client.search(
    collection_name=collection_name,
    data=embedding_model.encode_queries(
        [question]
    ),  # 将问题转换为嵌入向量
    limit=300,  # 返回前3个结果
    search_params={"metric_type": "IP", "params": {}},  # 内积距离
    output_fields=["text"],  # 返回 text 字段
)

让我们看一下查询的搜索结果

In [22]:
import json

retrieved_lines_with_distances = [
    (res["entity"]["text"], res["distance"]) for res in search_res[0]
]
print(json.dumps(retrieved_lines_with_distances, indent=4))

[
    [
        " \u503a\u52a1\u4eba\u5c65\u884c\u503a\u52a1\u6216\u8005\u62c5\u4fdd\u7269\u6743\u6d88\u706d\u7684\uff0c\u62c5\u4fdd\u7269\u6743\u6d88\u706d\u3002\n\n",
        0.7803130745887756
    ],
    [
        " \u62c5\u4fdd\u7269\u6743\u6d88\u706d\u7684\uff0c\u767b\u8bb0\u673a\u6784\u5e94\u5f53\u4f9d\u6cd5\u529e\u7406\u6ce8\u9500\u767b\u8bb0\u3002\n\n##### \u7b2c\u4e8c\u8282 \u62b5\u62bc\u6743\n\n",
        0.7277718186378479
    ],
    [
        " \u8d28\u6743\u6d88\u706d\u7684\uff0c\u767b\u8bb0\u673a\u6784\u5e94\u5f53\u4f9d\u6cd5\u529e\u7406\u6ce8\u9500\u767b\u8bb0\u3002\n\u8d28\u6743\u4eba\u5e94\u5f53\u5c06\u4e0d\u52a8\u4ea7\u767b\u8bb0\u7c3f\u8bb0\u8f7d\u7684\u8d28\u6743\u6ce8\u9500\u3002\n\n",
        0.7129852771759033
    ],
    [
        " \u503a\u52a1\u4eba\u5c65\u884c\u503a\u52a1\u6216\u8005\u7559\u7f6e\u6743\u6d88\u706d\u7684\uff0c\u7559\u7f6e\u6743\u6d88\u706d\u3002\n\n",
        0.7103036642074585
    ],
    [
        " \u7528\u76ca\u7269\u6743\u6d88\u706d\u7684\uf

### 使用 LLM 获取 RAG 响应

将检索到的文档转换为字符串格式。

In [23]:
context = "\n".join(
    [line_with_distance[0] for line_with_distance in retrieved_lines_with_distances]
)

In [24]:
context

' 债务人履行债务或者担保物权消灭的，担保物权消灭。\n\n\n 担保物权消灭的，登记机构应当依法办理注销登记。\n\n##### 第二节 抵押权\n\n\n 质权消灭的，登记机构应当依法办理注销登记。\n质权人应当将不动产登记簿记载的质权注销。\n\n\n 债务人履行债务或者留置权消灭的，留置权消灭。\n\n\n 用益物权消灭的，登记机构应当依法办理注销登记。\n\n\n 最高额抵押权消灭的，登记机构应当依法办理注销登记。\n抵押权人应当将不动产登记簿记载的抵押权注销。\n\n##### 第三节 质权\n\n###### 一、动产质权\n\n\n 抵押权消灭的，登记机构应当依法办理注销登记。\n抵押权人应当将不动产登记簿记载的抵押权注销。\n\n\n 抵押权消灭的，登记机构应当依法办理注销登记。\n抵押权人应当将不动产登记簿记载的抵押权注销。\n\n\n 质权消灭的，登记机构应当依法办理注销登记。\n质权人应当将不动产登记簿记载的质权注销。\n\n###### 二、权利质权\n\n\n 担保物权包括抵押权、质权和留置权。\n\n\n 法律、行政法规对担保物权有特别规定的，依照其规定。\n\n\n 法律、行政法规对担保物权有特别规定的，依照其规定。\n\n\n 抵押财产被征收、征用、毁损或者灭失的，抵押权人有权就获得的补偿金、赔偿金或者保险金等优先受偿。\n\n\n 质押财产被征收、征用、毁损或者灭失的，质权人有权就获得的补偿金、赔偿金或者保险金等优先受偿。\n\n\n 当事人签订买卖房屋的协议或者签订其他不动产物权的协议，为保障将来实现物权，可以依照约定向登记机构申请预告登记。预告登记后，未经预告登记的权利人同意，处分该不动产的，不发生物权效力。\n预告登记后，债权消灭或者自能够进行不动产登记之日起九十日内未申请登记的，预告登记失效。\n\n\n 债务人履行债务或者留置权消灭的，留置权消灭。\n\n#### 第五章 占有\n\n\n 担保物权人在债务人不履行到期债务或者发生当事人约定的实现担保物权的情形，有权依照法律规定以担保财产优先受偿。\n\n\n 担保物权人在债务人不履行到期债务或者发生当事人约定的实现担保物权的情形，有权依照法律规定以担保财产优先受偿。\n\n\n 抵押权人实现抵押权，可以与抵押人协议以抵押财产折价或者以拍卖、变卖该抵押财产所得的价款优先受

In [25]:
question

'担保物权消灭的'

为语言模型定义系统和用户提示。此提示是使用从 Milvus 检索到的文档组装而成的。

In [27]:
SYSTEM_PROMPT = """
Human: 你是一个 AI 助手。你能够从提供的上下文段落片段中找到问题的答案。
"""
USER_PROMPT = f"""
请使用以下用 <context> 标签括起来的信息片段来回答用 <question> 标签括起来的问题。最后追加原始回答的中文翻译，并用 <translated>和</translated> 标签标注。
<context>
{context}
</context>
<question>
{question}
</question>
<translated>
</translated>
"""

In [28]:
USER_PROMPT

'\n请使用以下用 <context> 标签括起来的信息片段来回答用 <question> 标签括起来的问题。最后追加原始回答的中文翻译，并用 <translated>和</translated> 标签标注。\n<context>\n 债务人履行债务或者担保物权消灭的，担保物权消灭。\n\n\n 担保物权消灭的，登记机构应当依法办理注销登记。\n\n##### 第二节 抵押权\n\n\n 质权消灭的，登记机构应当依法办理注销登记。\n质权人应当将不动产登记簿记载的质权注销。\n\n\n 债务人履行债务或者留置权消灭的，留置权消灭。\n\n\n 用益物权消灭的，登记机构应当依法办理注销登记。\n\n\n 最高额抵押权消灭的，登记机构应当依法办理注销登记。\n抵押权人应当将不动产登记簿记载的抵押权注销。\n\n##### 第三节 质权\n\n###### 一、动产质权\n\n\n 抵押权消灭的，登记机构应当依法办理注销登记。\n抵押权人应当将不动产登记簿记载的抵押权注销。\n\n\n 抵押权消灭的，登记机构应当依法办理注销登记。\n抵押权人应当将不动产登记簿记载的抵押权注销。\n\n\n 质权消灭的，登记机构应当依法办理注销登记。\n质权人应当将不动产登记簿记载的质权注销。\n\n###### 二、权利质权\n\n\n 担保物权包括抵押权、质权和留置权。\n\n\n 法律、行政法规对担保物权有特别规定的，依照其规定。\n\n\n 法律、行政法规对担保物权有特别规定的，依照其规定。\n\n\n 抵押财产被征收、征用、毁损或者灭失的，抵押权人有权就获得的补偿金、赔偿金或者保险金等优先受偿。\n\n\n 质押财产被征收、征用、毁损或者灭失的，质权人有权就获得的补偿金、赔偿金或者保险金等优先受偿。\n\n\n 当事人签订买卖房屋的协议或者签订其他不动产物权的协议，为保障将来实现物权，可以依照约定向登记机构申请预告登记。预告登记后，未经预告登记的权利人同意，处分该不动产的，不发生物权效力。\n预告登记后，债权消灭或者自能够进行不动产登记之日起九十日内未申请登记的，预告登记失效。\n\n\n 债务人履行债务或者留置权消灭的，留置权消灭。\n\n#### 第五章 占有\n\n\n 担保物权人在债务人不履行到期债务或者发生当事人约定的实现担保物权的情形，有权依照法律规定以担保财产优先受

使用 DeepSeek 提供的 `deepseek-chat` 模型根据提示生成响应。

In [31]:
response = deepseek_client.chat.completions.create(
    model="deepseek-chat",
    messages=[
        {"role": "system", "content": SYSTEM_PROMPT},
        {"role": "user", "content": USER_PROMPT},
    ],
)
print(response.choices[0].message.content)

根据提供的上下文，担保物权消灭的情形包括：

1. **债务人履行债务**：当债务人履行了其债务时，担保物权消灭。
2. **担保物权消灭的其他情形**：根据上下文，担保物权消灭后，登记机构应当依法办理注销登记。此外，留置权在债务人履行债务或留置权消灭时也消灭。

具体条文依据：
- "债务人履行债务或者担保物权消灭的，担保物权消灭。"
- "债务人履行债务或者留置权消灭的，留置权消灭。"

因此，担保物权消灭的主要原因是债务人履行债务，或者担保物权因其他法定情形（如留置权消灭）而消灭。

<translated>
担保物权消灭的情形包括：
1. **债务人履行债务**：当债务人履行了其债务时，担保物权消灭。
2. **担保物权消灭的其他情形**：根据上下文，担保物权消灭后，登记机构应当依法办理注销登记。此外，留置权在债务人履行债务或留置权消灭时也消灭。

具体条文依据：
- "债务人履行债务或者担保物权消灭的，担保物权消灭。"
- "债务人履行债务或者留置权消灭的，留置权消灭。"

因此，担保物权消灭的主要原因是债务人履行债务，或者担保物权因其他法定情形（如留置权消灭）而消灭。
</translated>
